In [2]:
# Importing modules
import numpy as np
import pandas as pd
import requests
import os
import re
from urllib.parse import urlparse
from pathlib import Path
import os
import cv2
import random
from PIL import Image, ImageEnhance
import shutil
from collections import Counter
import tensorflow as tf
from tensorflow import keras
import json
import keras
from tensorflow.keras import layers, models, regularizers
from tensorflow.keras.layers import InputLayer, RandomFlip, RandomRotation, RandomZoom, Conv2D, MaxPooling2D, Flatten, Dense, Dropout, BatchNormalization
from tensorflow.keras.models import load_model, Sequential
from tensorflow.keras.preprocessing import image
from tensorflow.keras.preprocessing.image import ImageDataGenerator, load_img, img_to_array
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau
from scipy.ndimage import rotate, geometric_transform
from tensorflow.image import resize_with_crop_or_pad
from tensorflow.keras.optimizers import Adam
import warnings
warnings.filterwarnings('ignore')
import matplotlib.pyplot as plt
from sklearn.metrics import classification_report, confusion_matrix

In [4]:
# Reading the json file retrieved from the github (to be modified to use API)
sets = pd.read_json(r"C:\Users\Jimmy\Desktop\cb-ds-19\00_Projects\ds-final-project-main\en.json")

In [5]:
# Taking a peek inside of the json file
sets.head()

id                       name series  printedTotal  total  \
0  base1                       Base   Base           102    102   
1  base2                     Jungle   Base            64     64   
2  basep  Wizards Black Star Promos   Base            53     53   
3  base3                     Fossil   Base            62     62   
4  base4                 Base Set 2   Base           130    130   

               legalities ptcgoCode releaseDate            updatedAt  \
0  {'unlimited': 'Legal'}        BS  1999/01/09  2022/10/10 15:12:00   
1  {'unlimited': 'Legal'}        JU  1999/06/16  2020/08/14 09:35:00   
2  {'unlimited': 'Legal'}        PR  1999/07/01  2020/08/14 09:35:00   
3  {'unlimited': 'Legal'}        FO  1999/10/10  2020/08/14 09:35:00   
4  {'unlimited': 'Legal'}        B2  2000/02/24  2022/10/10 15:12:00   

                                              images  
0  {'symbol': 'https://images.pokemontcg.io/base1...  
1  {'symbol': 'https://images.pokemontcg.io/base2...  
2  {'symbol': 'https://images.pokemontcg.io/basep...  
3  {'symbol': 'https://images.pokemontcg.io/base3...  
4  {'symbol': 'https://images.pokemontcg.io/base4...

In [6]:
# images column contains dictionary. extract those to their own columns (we only care about symbol) and drop images column
images_sets = sets['images'].apply(pd.Series)

sets = pd.concat([sets.drop('images', axis = 1),images_sets], axis = 1)

sets.head()

id                       name series  printedTotal  total  \
0  base1                       Base   Base           102    102   
1  base2                     Jungle   Base            64     64   
2  basep  Wizards Black Star Promos   Base            53     53   
3  base3                     Fossil   Base            62     62   
4  base4                 Base Set 2   Base           130    130   

               legalities ptcgoCode releaseDate            updatedAt  \
0  {'unlimited': 'Legal'}        BS  1999/01/09  2022/10/10 15:12:00   
1  {'unlimited': 'Legal'}        JU  1999/06/16  2020/08/14 09:35:00   
2  {'unlimited': 'Legal'}        PR  1999/07/01  2020/08/14 09:35:00   
3  {'unlimited': 'Legal'}        FO  1999/10/10  2020/08/14 09:35:00   
4  {'unlimited': 'Legal'}        B2  2000/02/24  2022/10/10 15:12:00   

                                          symbol  \
0  https://images.pokemontcg.io/base1/symbol.png   
1  https://images.pokemontcg.io/base2/symbol.png   
2  https://images.pokemontcg.io/basep/symbol.png   
3  https://images.pokemontcg.io/base3/symbol.png   
4  https://images.pokemontcg.io/base4/symbol.png   

                                          logo  
0  https://images.pokemontcg.io/base1/logo.png  
1  https://images.pokemontcg.io/base2/logo.png  
2  https://images.pokemontcg.io/basep/logo.png  
3  https://images.pokemontcg.io/base3/logo.png  
4  https://images.pokemontcg.io/base4/logo.png

In [19]:
# Download all of the logo images as 001.jpg in a folder named after the set (using name column from sets), which is in term inside of a folder named after series

# Define base path location of all the images
base_path = r"C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol"

# Function to sanitize folder names
def sanitize_folder_name(name):
    # Replace invalid characters with an underscore or remove them
    return re.sub(r'[<>:"/\\|?*]', '', name)

# Function to download and save an image as train.jpg in the specified folder
def download_image(url, series, name, base_path):
    # Sanitize the series and name to create valid folder names
    series_safe = sanitize_folder_name(series)
    name_safe = sanitize_folder_name(name)

    # Construct the full path using base_path, sanitized series, and name
    final_folder_path = os.path.join(base_path, series_safe, name_safe)

    # Ensure the target folder exists
    os.makedirs(final_folder_path, exist_ok=True)

    # Full path to save the image as 001.jpg
    file_path = os.path.join(final_folder_path, '001.jpg')

    try:
        # Send a GET request to fetch the image
        response = requests.get(url)
        response.raise_for_status()  # Check if the request was successful

        # Save the image to the specified path
        with open(file_path, 'wb') as f:
            f.write(response.content)

        print(f"Downloaded 001.jpg to {final_folder_path}")
    except requests.exceptions.RequestException as e:
        print(f"Failed to download train.jpg for {series_safe}/{name_safe}: {e}")

# Loop through the DataFrame and download images
for index, row in sets.iterrows():
    download_image(row['symbol'], row['series'], row['name'], base_path)

Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base
Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Jungle
Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Wizards Black Star Promos
Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Fossil
Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base Set 2
Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Team Rocket
Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Gym\Gym Heroes
Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Gym\Gym Challenge
Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Neo\Neo Genesis
Downloaded 001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Neo\Neo Discovery
Downloaded 001.jpg to C:\

In [20]:
# Base symbol is incorrect. The absence of an image should indicate base set
file_path = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\001.jpg'

# Check if the file exists before trying to remove it
if os.path.exists(file_path):
    os.remove(file_path)
    print(f"Removed file: {file_path}")
else:
    print(f"File not found: {file_path}")

# Create a dummy blank image so that the model training is not imbalanced
def create_blank_image(width, height, color=(255, 255, 255, 0), save_path="001.png"):
    # Create a new image with the specified size and color
    image = Image.new('RGB', (width, height), color)

    # Save the image
    image.save(save_path, 'JPEG')
    print(f"Blank image saved at: {save_path}")

# Example usage:
# Create a blank image of size 256x256 with a white background
output_directory = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base'
os.makedirs(output_directory, exist_ok=True)

# Path for the single blank image
blank_image_path = os.path.join(output_directory, '001.jpg')

# Create and save the blank image
create_blank_image(width=256, height=256, color=(255, 255, 255), save_path=blank_image_path)

Removed file: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\001.jpg
Blank image saved at: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\001.jpg


In [21]:
# Base path
base_path = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol'

def process_directories(base_path):
    # Define the target directory path
    target_directory = os.path.join(base_path, 'Black Star Promos', 'Black Star Promos')
    os.makedirs(target_directory, exist_ok=True)
    print(f"Created target directory: {target_directory}")

    # Initialize a list to collect paths of '001.jpg' files found
    jpg_files_to_copy = []

    # Iterate through all subdirectories in the base path
    for series_dir in os.listdir(base_path):
        series_path = os.path.join(base_path, series_dir)
        print(f"Processing series directory: {series_path}")

        # Skip the main 'Black Star Promos' directory if it exists
        if not os.path.isdir(series_path) or series_dir == 'Black Star Promos':
            print(f"Skipping non-directory or target directory: {series_path}")
            continue

        # Iterate through all directories within each series directory
        for promo_dir in os.listdir(series_path):
            promo_path = os.path.join(series_path, promo_dir)
            print(f"Processing promo directory: {promo_path}")

            # Check if the directory name ends with 'Black Star Promos'
            if not os.path.isdir(promo_path) or not promo_dir.endswith('Black Star Promos'):
                print(f"Skipping directory: {promo_path}")
                continue

            # Look for the '001.jpg' file
            jpg_file = os.path.join(promo_path, '001.jpg')
            print(f"Looking for file: {jpg_file}")

            if os.path.isfile(jpg_file):
                # Collect the path of the '001.jpg' file to copy later
                jpg_files_to_copy.append(jpg_file)
                print(f"Found file: {jpg_file}")
            else:
                print(f"File not found: {jpg_file}")

    # If any '001.jpg' files were found, randomly select one and copy it to the target directory
    if jpg_files_to_copy:
        selected_jpg = random.choice(jpg_files_to_copy)
        print(f"Selected file to copy: {selected_jpg}")
        
        # Check if the target directory exists
        if not os.path.exists(target_directory):
            print(f"Target directory {target_directory} does not exist.")
            return

        try:
            # Full path for the copied file
            destination_path = os.path.join(target_directory, os.path.basename(selected_jpg))
            shutil.copy(selected_jpg, destination_path)
            print(f"Copied {selected_jpg} to {destination_path}")
        except Exception as e:
            print(f"Error copying file {selected_jpg}: {e}")

        # After copying, delete the original directories
        for jpg_file in jpg_files_to_copy:
            promo_path = os.path.dirname(jpg_file)
            try:
                shutil.rmtree(promo_path)
                print(f"Deleted directory: {promo_path}")
            except Exception as e:
                print(f"Error deleting directory {promo_path}: {e}")
    else:
        print("No '001.jpg' files found to copy.")

# Execute the function
process_directories(base_path)


Created target directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Black Star Promos\Black Star Promos
Processing series directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base
Processing promo directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base
Skipping directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base
Processing promo directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base Set 2
Skipping directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base Set 2
Processing promo directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Fossil
Skipping directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Fossil
Processing promo directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Jungle
Skipping directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Jungle
Processing promo direc

In [22]:
# Duplicate folders for subsets need to be removed as they are not actually distinct classes
def delete_folders_with_phrases(base_path, phrases):
    # Iterate through all subdirectories in the base path
    for root, dirs, files in os.walk(base_path, topdown=False):
        print(f"Processing directory: {root}")
        for dir_name in dirs:
            dir_path = os.path.join(root, dir_name)
            print(f"Checking directory: {dir_path}")

            # Check if the directory name contains any of the specified phrases
            if any(phrase in dir_name for phrase in phrases):
                print(f"Found matching directory: {dir_path}")
                # Remove the directory and its contents
                try:
                    shutil.rmtree(dir_path)
                    print(f"Deleted directory: {dir_path}")
                except Exception as e:
                    print(f"Error deleting directory {dir_path}: {e}")

# Phrases to look for in directory names
phrases = ["Trainer Gallery", "Galarian Gallery", "Shining Fates Shiny Vault"]

# Delete folders that contain any of the phrases
delete_folders_with_phrases(base_path, phrases)

Processing directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base
Processing directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base Set 2
Processing directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Fossil
Processing directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Jungle
Processing directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Team Rocket
Processing directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base
Checking directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base
Checking directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base Set 2
Checking directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Fossil
Checking directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Jungle
Checking directory: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symb

In [23]:
# Only 1 example of each symbol is available. In order to train, we are bulking out our training set (and creating images that will be used for test/valid set) by applying our data augmentation to the image and exporting them as images.
# Custom functions for performing data augmentation. Early testing showed that extreme data augmentation shifted the images outside of the usable image space
def random_invert_black_and_white(image, invert_prob=0.5):
    if random.random() < invert_prob:
        grayscale_image = np.mean(image, axis=-1)
        inverted_image = 255 - grayscale_image
        return np.stack([inverted_image] * 3, axis=-1).astype('uint8')
    else:
        return image.astype('uint8')

def adjust_brightness_contrast_saturation(image, brightness=0.1, contrast=0.1, saturation=0.1):
    pil_image = Image.fromarray(image.astype('uint8')).convert('RGB')

    # Apply random brightness
    enhancer = ImageEnhance.Brightness(pil_image)
    pil_image = enhancer.enhance(1 + random.uniform(-brightness, brightness))

    # Apply random contrast
    enhancer = ImageEnhance.Contrast(pil_image)
    pil_image = enhancer.enhance(1 + random.uniform(-contrast, contrast))

    # Apply random saturation
    enhancer = ImageEnhance.Color(pil_image)
    pil_image = enhancer.enhance(1 + random.uniform(-saturation, saturation))

    return np.array(pil_image).astype('uint8')

def add_gaussian_noise(image, mean=0, std=25):
    noise = np.random.normal(mean, std, image.shape)
    noisy_image = image + noise
    return np.clip(noisy_image, 0, 255).astype('uint8')

def apply_blur(image, kernel_size=3):
    blurred_image = cv2.GaussianBlur(image, (kernel_size, kernel_size), 0)
    return blurred_image.astype('uint8')

def apply_shiny_overlay(image, alpha=0.3):
    overlay = np.ones_like(image) * 255  # White overlay
    shiny_image = cv2.addWeighted(image.astype('uint8'), 1 - alpha, overlay.astype('uint8'), alpha, 0)
    return shiny_image.astype('uint8')

def add_random_shadow(image, shadow_intensity=0.5):
    shadow_mask = np.random.uniform(0.3, 1.0, size=(image.shape[0], image.shape[1], 1))
    shadow_mask = np.repeat(shadow_mask, 3, axis=-1)
    shadow_image = np.clip(image * shadow_mask, 0, 255).astype('uint8')
    return shadow_image

def rotate_and_keep_shape(image, angle):
    pil_image = Image.fromarray(image.astype('uint8'))
    rotated_image = pil_image.rotate(angle, resample=Image.BICUBIC, fillcolor=(0, 0, 0))
    return np.array(rotated_image).astype('uint8')

def ensure_consistent_dimensions(image, target_height, target_width):
    pil_image = Image.fromarray(image)
    pil_image = pil_image.resize((target_width, target_height), Image.BICUBIC)
    return np.array(pil_image).astype('uint8')

def zoom_and_pad(image, zoom_factor):
    pil_image = Image.fromarray(image.astype('uint8'))
    width, height = pil_image.size

    new_width = int(width * zoom_factor)
    new_height = int(height * zoom_factor)

    zoomed_image = pil_image.resize((new_width, new_height), resample=Image.BICUBIC)

    left = (new_width - width) / 2
    top = (new_height - height) / 2
    right = (new_width + width) / 2
    bottom = (new_height + height) / 2

    zoomed_image = zoomed_image.crop((left, top, right, bottom))

    # Ensure consistent dimensions
    target_height, target_width = height, width
    return ensure_consistent_dimensions(np.array(zoomed_image), target_height, target_width)

def custom_augmentation(image):

    if random.random() < 0.3:
        image = random_invert_black_and_white(image, invert_prob=0.5)
    if random.random() < 0.4:
        image = adjust_brightness_contrast_saturation(image, brightness=0.2, contrast=0.2, saturation=0.2)
    if random.random() < 0.4:
        image = add_gaussian_noise(image, mean=0, std=15)
    if random.random() < 0.3:
        image = apply_blur(image, kernel_size=3)
    if random.random() < 0.3:
        image = apply_shiny_overlay(image, alpha=0.2)
    if random.random() < 0.4:
        image = add_random_shadow(image, shadow_intensity=0.5)
    if random.random() < 0.9:
        rotation_angle = random.uniform(-180, 180)
        image = rotate_and_keep_shape(image, rotation_angle)
    if random.random() < 0.8:
        zoom_factor = random.uniform(0.4, 1.2)
        image = zoom_and_pad(image, zoom_factor)
    return image

def process_image(image_path, save_directory):
    try:
        # Prepare ImageDataGenerator
        image = load_img(image_path)
        image_array = img_to_array(image)
        image_array = image_array.reshape((1,) + image_array.shape)

        datagen = ImageDataGenerator(
            shear_range=0.5,
            horizontal_flip=False,
            vertical_flip=False,
            fill_mode='nearest',
            preprocessing_function=custom_augmentation
        )

        iterator = datagen.flow(image_array, batch_size=1)

        # Generate and save 199 augmented images
        for i in range(2, 201):
            try:
                batch = next(iterator)
                augmented_image = batch[0].astype('uint8')

                # Ensure the image is in RGBA format
                if augmented_image.shape[-1] == 3:
                    alpha_channel = np.ones((augmented_image.shape[0], augmented_image.shape[1]), dtype='uint8') * 255
                    augmented_image = np.dstack((augmented_image, alpha_channel))

                # Save the image with leading zeros in the filename
                save_path = os.path.join(save_directory, f"{i:03}.png")
                Image.fromarray(augmented_image, 'RGBA').save(save_path, format='PNG')

                print(f"Saved image to {save_path}")

            except Exception as e:
                print(f"Error processing image {i}: {e}")

    except Exception as e:
        print(f"Error processing image {image_path}: {e}")

# Walk through the directory tree
for root, dirs, files in os.walk(base_path):
    for file in files:
        if file.lower() == "001.jpg":
            image_path = os.path.join(root, file)
            save_directory = root
            print(f"Processing {image_path}")
            process_image(image_path, save_directory)

Processing C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\001.jpg
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\002.png
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\003.png
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\004.png
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\005.png
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\006.png
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\007.png
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\008.png
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\009.png
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\010.png
Saved image to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\

In [24]:
# Originally downloaded 001.jpg should be converted to RGBA and converted to .png filetype

# Function to convert .jpg to .png with RGBA format
def convert_jpg_to_png_with_rgba(jpg_path, png_path):
    with Image.open(jpg_path) as img:
        rgba_img = img.convert('RGBA')
        rgba_img.save(png_path)

# Traverse the directory structure
for root, dirs, files in os.walk(base_path):
    for file in files:
        if file.lower().endswith('.jpg'):
            # Full path to the .jpg file
            jpg_path = os.path.join(root, file)
            
            # Change the file extension to .png
            png_file = os.path.splitext(file)[0] + '.png'
            
            # Full path to the new .png file
            png_path = os.path.join(root, png_file)
            
            # Convert and save the image
            convert_jpg_to_png_with_rgba(jpg_path, png_path)

            # Remove the original .jpg file
            os.remove(jpg_path)

            print(f"Converted {jpg_path} to {png_path} and deleted the original file.")

Converted C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base\001.png and deleted the original file.
Converted C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base Set 2\001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base Set 2\001.png and deleted the original file.
Converted C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Fossil\001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Fossil\001.png and deleted the original file.
Converted C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Jungle\001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Jungle\001.png and deleted the original file.
Converted C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Team Rocket\001.jpg to C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Team Rocket\001.png and del

In [25]:
# Create the CNN folder
cnn_base_path = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN'

os.makedirs(cnn_base_path, exist_ok=True)

# Create the train, test, and valid subfolders inside CNN
train_base_path = os.path.join(cnn_base_path, 'train')
test_base_path = os.path.join(cnn_base_path, 'test')
valid_base_path = os.path.join(cnn_base_path, 'valid')

os.makedirs(train_base_path, exist_ok=True)
os.makedirs(test_base_path, exist_ok=True)
os.makedirs(valid_base_path, exist_ok=True)

# Iterate over each series (ignore `train`, `test`, `valid` from Set_Symbol)
for series in os.listdir(base_path):
    series_path = os.path.join(base_path, series)

    if not os.path.isdir(series_path):
        continue

    # Iterate over each "name" folder within the series
    for name_folder in os.listdir(series_path):
        name_folder_path = os.path.join(series_path, name_folder)

        if not os.path.isdir(name_folder_path):
            continue

        print(f"Processing folder: {name_folder_path}")

        # Collect .jpg and .png images
        images = []
        for file in os.listdir(name_folder_path):
            file_path = os.path.join(name_folder_path, file)
            if file.lower().endswith(('.jpg', '.png')):
                images.append(file_path)

        # Debugging: Check the number of images found
        num_images = len(images)
        print(f"Found {num_images} images in {name_folder_path}.")

        # Create a subfolder under train, test, and valid named after `name_folder`
        os.makedirs(os.path.join(train_base_path, name_folder), exist_ok=True)
        os.makedirs(os.path.join(valid_base_path, name_folder), exist_ok=True)
        os.makedirs(os.path.join(test_base_path, name_folder), exist_ok=True)

        if num_images < 20:
            print(f"Warning: Not enough images in {name_folder_path}. Found {num_images} images. The folders will be empty.")
            continue

        # Shuffle images randomly
        random.shuffle(images)

        # Calculate split sizes
        num_train = int(0.45 * num_images)
        num_valid = int(0.45 * num_images)
        num_test = min(num_images - num_train - num_valid, 20)

        # Select images for train, valid, and test
        train_images = images[:num_train]
        valid_images = images[num_train:num_train + num_valid]
        test_images = images[num_train + num_valid:num_train + num_valid + num_test]

        # Copy images to their respective subfolders with new names
        for idx, img_path in enumerate(train_images):
            new_filename = f"train{str(idx + 1).zfill(3)}{os.path.splitext(img_path)[1]}"
            shutil.copy(img_path, os.path.join(train_base_path, name_folder, new_filename))

        for idx, img_path in enumerate(valid_images):
            new_filename = f"valid{str(idx + 1).zfill(3)}{os.path.splitext(img_path)[1]}"
            shutil.copy(img_path, os.path.join(valid_base_path, name_folder, new_filename))

        for idx, img_path in enumerate(test_images):
            new_filename = f"test{str(idx + 1).zfill(3)}{os.path.splitext(img_path)[1]}"
            shutil.copy(img_path, os.path.join(test_base_path, name_folder, new_filename))

print("Images have been successfully copied and renamed into CNN/train, CNN/test, and CNN/valid subfolders.")

Processing folder: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base
Found 200 images in C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base.
Processing folder: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base Set 2
Found 200 images in C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Base Set 2.
Processing folder: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Fossil
Found 200 images in C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Fossil.
Processing folder: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Jungle
Found 200 images in C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Jungle.
Processing folder: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Team Rocket
Found 200 images in C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbol\Base\Team Rocket.
Processing folder: C:\Users\Jimmy\Desktop\final-project\PokemonTCG\Set_Symbo

In [26]:
cnn_base_path = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN'

def directory_contains_files(path):
    """Check if a directory contains any files."""
    if not os.path.exists(path):
        return False
    return any(os.path.isfile(os.path.join(path, f)) for f in os.listdir(path))

# Loop through each split directory (train, test, valid) directly within base_path
for split in ['train', 'test', 'valid']:
    split_path = os.path.join(cnn_base_path, split)

    if not os.path.isdir(split_path):
        print(f"{split_path} does not exist or is not a directory.")
        continue

    # Loop through each "name" folder within the split
    for name_folder in os.listdir(split_path):
        name_folder_path = os.path.join(split_path, name_folder)

        if not os.path.isdir(name_folder_path):
            continue

        # Check and print if the directory contains files
        has_files = directory_contains_files(name_folder_path)

        print(f"{split} path {name_folder_path} contains files: {has_files}")

train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\151 contains files: True
train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\Ancient Origins contains files: True
train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\Aquapolis contains files: True
train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\Arceus contains files: True
train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\Astral Radiance contains files: True
train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\Base contains files: True
train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\Base Set 2 contains files: True
train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\Battle Styles contains files: True
train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\Best of Game contains files: True
train path C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train\Black & White contains fi

In [27]:
def count_folders(path):
    """Count the number of folders (subdirectories) in a given directory."""
    if not os.path.isdir(path):
        return 0
    return len([d for d in os.listdir(path) if os.path.isdir(os.path.join(path, d))])

# Iterate over the new train, test, and valid directories within CNN
for split in ['train', 'test', 'valid']:
    split_path = os.path.join(cnn_base_path, split)

    # Ensure that the split_path exists and is a directory
    if not os.path.isdir(split_path):
        print(f"Directory does not exist: {split_path}")
        continue

    # Count the number of folders inside the split_path
    num_folders = count_folders(split_path)
    print(f"Number of folders in {split_path}: {num_folders}")

Number of folders in C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train: 147
Number of folders in C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\test: 147
Number of folders in C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\valid: 147


In [28]:
def count_files_in_folder(folder_path):
    """Count the number of files in a given folder."""
    if not os.path.isdir(folder_path):
        return 0
    return len([f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))])

def count_folders(path):
    """Count the number of folders (subdirectories) in a given directory."""
    if not os.path.isdir(path):
        return 0
    return len([d for d in os.listdir(path) if os.path.isdir(os.path.join(path, d))])

# Iterate over the new train, test, and valid directories within CNN
for split in ['train', 'test', 'valid']:
    split_path = os.path.join(cnn_base_path, split)

    # Ensure that the split_path exists and is a directory
    if not os.path.isdir(split_path):
        print(f"Directory does not exist: {split_path}")
        continue

    # Count the number of folders inside the split_path
    folders = [d for d in os.listdir(split_path) if os.path.isdir(os.path.join(split_path, d))]
    num_folders = len(folders)

    print(f"Number of folders in {split_path}: {num_folders}")

    # Iterate over each folder to count the number of files
    for folder in folders:
        folder_path = os.path.join(split_path, folder)
        num_files = count_files_in_folder(folder_path)
        print(f"  Number of files in folder '{folder}': {num_files}")

Number of folders in C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN\train: 147
  Number of files in folder '151': 90
  Number of files in folder 'Ancient Origins': 90
  Number of files in folder 'Aquapolis': 90
  Number of files in folder 'Arceus': 90
  Number of files in folder 'Astral Radiance': 90
  Number of files in folder 'Base': 90
  Number of files in folder 'Base Set 2': 90
  Number of files in folder 'Battle Styles': 90
  Number of files in folder 'Best of Game': 90
  Number of files in folder 'Black & White': 90
  Number of files in folder 'Black Star Promos': 90
  Number of files in folder 'Boundaries Crossed': 90
  Number of files in folder 'BREAKpoint': 90
  Number of files in folder 'BREAKthrough': 90
  Number of files in folder 'Brilliant Stars': 90
  Number of files in folder 'Burning Shadows': 90
  Number of files in folder 'Call of Legends': 90
  Number of files in folder 'Celebrations': 90
  Number of files in folder 'Celebrations Classic Collection': 90
  Numb

In [7]:
# Define paths
cnn_base_path = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN'
train_path = os.path.join(cnn_base_path, 'train')
valid_path = os.path.join(cnn_base_path, 'valid')

# Define image size and batch size
target_size = (150, 150)
batch_size = 32

# Create ImageDataGenerator instance for training and validation
train_datagen = ImageDataGenerator(
    rescale=1./255
)

valid_datagen = ImageDataGenerator(
    rescale=1./255
)

# Create training and validation data generator
train_generator = train_datagen.flow_from_directory(
    train_path,
    target_size=target_size,
    batch_size=batch_size,
    class_mode='categorical',
    shuffle=True
)

valid_generator = valid_datagen.flow_from_directory(
    valid_path,
    target_size=target_size,
    batch_size=batch_size,
    class_mode='categorical',
    shuffle=False
)

# Check how many images and classes are loaded
num_train_images = train_generator.samples
num_classes = len(train_generator.class_indices)

print(f"Number of training images: {num_train_images}")
print(f"Number of classes: {num_classes}")

num_valid_images = valid_generator.samples
print(f"Number of validation images: {num_valid_images}")

Found 13230 images belonging to 147 classes.
Found 13230 images belonging to 147 classes.
Number of training images: 13230
Number of classes: 147
Number of validation images: 13230


In [11]:
# Define CNN model
model = Sequential([
    InputLayer(input_shape=(150, 150, 3)),
    layers.Conv2D(16, (3, 3), activation=keras.activations.swish, kernel_regularizer=regularizers.l2(0.001)),
    BatchNormalization(),
    MaxPooling2D((2, 2)),

    Conv2D(32, (3, 3), activation='relu', kernel_regularizer=regularizers.l2(0.001)),
    BatchNormalization(),
    MaxPooling2D((2, 2)),

    Conv2D(64, (3, 3), activation='relu', kernel_regularizer=regularizers.l2(0.001)),
    BatchNormalization(),
    MaxPooling2D((2, 2)),

    Conv2D(128, (3, 3), activation='relu', kernel_regularizer=regularizers.l2(0.001)),
    BatchNormalization(),
    MaxPooling2D((2, 2)),

    Flatten(),

    Dense(512, activation='relu', kernel_regularizer=regularizers.l2(0.001)),
    BatchNormalization(),
    Dropout(0.5),

    Dense(num_classes, activation='softmax')
])

# Compile model
model.compile(
    optimizer=Adam(learning_rate=0.0005),
    loss='categorical_crossentropy',
    metrics=['accuracy']
)

# Print model summary
model.summary()

Model: "sequential_2"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d_8 (Conv2D)               │ (None, 148, 148, 16)   │           448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_10          │ (None, 148, 148, 16)   │            64 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_8 (MaxPooling2D)  │ (None, 74, 74, 16)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_9 (Conv2D)               │ (None, 72, 72, 32)     │         4,640 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_11          │ (None, 72, 72, 32)     │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_9 (MaxPooling2D)  │ (None, 36, 36, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_10 (Conv2D)              │ (None, 34, 34, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_12          │ (None, 34, 34, 64)     │           256 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_10 (MaxPooling2D) │ (None, 17, 17, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_11 (Conv2D)              │ (None, 15, 15, 128)    │        73,856 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_13          │ (None, 15, 15, 128)    │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_11 (MaxPooling2D) │ (None, 7, 7, 128)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten_2 (Flatten)             │ (None, 6272)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_4 (Dense)                 │ (None, 512)            │     3,211,776 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_14          │ (None, 512)            │         2,048 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 512)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_5 (Dense)                 │ (None, 147)            │        75,411 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 3,387,635 (12.92 MB)

 Trainable params: 3,386,131 (12.92 MB)

 Non-trainable params: 1,504 (5.88 KB)

In [31]:
# Define training callbacks
early_stopping = EarlyStopping(
    monitor='val_loss',
    patience=10,  # Number of epochs to wait before stopping if no improvement
    restore_best_weights=True
)

reduce_lr = ReduceLROnPlateau(
    monitor='val_loss',
    factor=0.2,  # Reduce learning rate by a factor of 0.2
    patience=5,  # Number of epochs with no improvement to wait before reducing
    min_lr=0.00001  # Minimum learning rate
)

# Define training parameters
epochs = 40  # Adjust based on your requirements

# Train the model
history = model.fit(
    train_generator,
    epochs=epochs,
    steps_per_epoch=train_generator.samples // batch_size,
    validation_data=valid_generator,
    validation_steps=valid_generator.samples // batch_size,
    callbacks=[early_stopping, reduce_lr]
)

# Save the model
model.save(r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\models\model01.keras')

Epoch 1/40
413/413 ━━━━━━━━━━━━━━━━━━━━ 270s 642ms/step - accuracy: 0.1244 - loss: 5.8265 - val_accuracy: 0.1705 - val_loss: 5.0980 - learning_rate: 5.0000e-04
Epoch 2/40
413/413 ━━━━━━━━━━━━━━━━━━━━ 0s 250us/step - accuracy: 0.3750 - loss: 3.8255 - val_accuracy: 0.2143 - val_loss: 4.7206 - learning_rate: 5.0000e-04
Epoch 3/40
413/413 ━━━━━━━━━━━━━━━━━━━━ 150s 362ms/step - accuracy: 0.5947 - loss: 2.8077 - val_accuracy: 0.6988 - val_loss: 2.3288 - learning_rate: 5.0000e-04
Epoch 4/40
413/413 ━━━━━━━━━━━━━━━━━━━━ 0s 125us/step - accuracy: 0.7500 - loss: 2.2634 - val_accuracy: 0.7143 - val_loss: 2.0573 - learning_rate: 5.0000e-04
Epoch 5/40
413/413 ━━━━━━━━━━━━━━━━━━━━ 150s 361ms/step - accuracy: 0.8053 - loss: 1.8901 - val_accuracy: 0.7861 - val_loss: 1.8825 - learning_rate: 5.0000e-04
Epoch 6/40
413/413 ━━━━━━━━━━━━━━━━━━━━ 0s 113us/step - accuracy: 0.7500 - loss: 2.0602 - val_accuracy: 0.7143 - val_loss: 1.8117 - learning_rate: 5.0000e-04
Epoch 7/40
413/413 ━━━━━━━━━━━━━━━━━━━━ 150s 3

FileNotFoundError: [Errno 2] No such file or directory: '/notebooks/PokemonTCG/models/model01.keras'

In [3]:
# Define paths
cnn_base_path = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN'
train_path = os.path.join(cnn_base_path, 'train')
valid_path = os.path.join(cnn_base_path, 'valid')

# Define image size and batch size
target_size2 = (150, 150)
batch_size2 = 16

# Create ImageDataGenerator instance for training and validation
train_datagen2 = ImageDataGenerator(
    rescale=1./255
)

valid_datagen2 = ImageDataGenerator(
    rescale=1./255
)

# Create training and validation data generator
train_generator2 = train_datagen2.flow_from_directory(
    train_path,
    target_size=target_size2,
    batch_size=batch_size2,
    class_mode='categorical',
    shuffle=True
)

valid_generator2 = valid_datagen2.flow_from_directory(
    valid_path,
    target_size=target_size2,
    batch_size=batch_size2,
    class_mode='categorical',
    shuffle=False
)

# Check how many images and classes are loaded
num_train_images2 = train_generator2.samples
num_classes2 = len(train_generator2.class_indices)

print(f"Number of training images: {num_train_images2}")
print(f"Number of classes: {num_classes2}")

num_valid_images2 = valid_generator2.samples
print(f"Number of validation images: {num_valid_images2}")

Found 13230 images belonging to 147 classes.
Found 13230 images belonging to 147 classes.
Number of training images: 13230
Number of classes: 147
Number of validation images: 13230


In [13]:
# Define training callbacks
early_stopping = EarlyStopping(
    monitor='val_loss',
    patience=10,  # Number of epochs to wait before stopping if no improvement
    restore_best_weights=True
)

reduce_lr = ReduceLROnPlateau(
    monitor='val_loss',
    factor=0.2,  # Reduce learning rate by a factor of 0.2
    patience=5,  # Number of epochs with no improvement to wait before reducing
    min_lr=0.00001  # Minimum learning rate
)

# Define training parameters
epochs = 40  # Adjust based on your requirements

# Train the model
history2 = model.fit(
    train_generator2,
    epochs=epochs,
    steps_per_epoch=train_generator2.samples // batch_size2,
    validation_data=valid_generator2,
    validation_steps=valid_generator.samples // batch_size2,
    callbacks=[early_stopping, reduce_lr]
)

# Save the model
model.save(r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\models\model03.keras')

Epoch 1/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 151s 179ms/step - accuracy: 0.1359 - loss: 5.6685 - val_accuracy: 0.5214 - val_loss: 3.1909 - learning_rate: 5.0000e-04
Epoch 2/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 0s 81us/step - accuracy: 0.3750 - loss: 3.6906 - val_accuracy: 0.5000 - val_loss: 2.6698 - learning_rate: 5.0000e-04
Epoch 3/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 146s 177ms/step - accuracy: 0.5912 - loss: 2.8451 - val_accuracy: 0.6802 - val_loss: 2.4119 - learning_rate: 5.0000e-04
Epoch 4/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 0s 55us/step - accuracy: 0.7500 - loss: 2.2920 - val_accuracy: 1.0000 - val_loss: 1.4961 - learning_rate: 5.0000e-04
Epoch 5/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 146s 176ms/step - accuracy: 0.7707 - loss: 2.0529 - val_accuracy: 0.8055 - val_loss: 1.9028 - learning_rate: 5.0000e-04
Epoch 6/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 0s 60us/step - accuracy: 0.6875 - loss: 2.0963 - val_accuracy: 0.9286 - val_loss: 1.5094 - learning_rate: 5.0000e-04
Epoch 7/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 146s 176m

In [35]:
# Define the directory for saving checkpoints
checkpoint_dir = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\models\checkpoints'
os.makedirs(checkpoint_dir, exist_ok=True)

# Function to build and train the model
def build_and_train_model(params, train_generator, valid_generator, epochs=20, batch_size=32):
    model = tf.keras.Sequential([
        InputLayer(input_shape=(150, 150, 3)),
        
        layers.Conv2D(
            filters=params['filters_1'],
            kernel_size=(3, 3),
            activation='relu',
            kernel_regularizer=regularizers.l2(params['l2_reg'])
        ),
        layers.BatchNormalization(),
        layers.MaxPooling2D((2, 2)),

        layers.Conv2D(
            filters=params['filters_2'],
            kernel_size=(3, 3),
            activation='relu',
            kernel_regularizer=regularizers.l2(params['l2_reg'])
        ),
        layers.BatchNormalization(),
        layers.MaxPooling2D((2, 2)),

        layers.Conv2D(
            filters=params['filters_3'],
            kernel_size=(3, 3),
            activation='relu',
            kernel_regularizer=regularizers.l2(params['l2_reg'])
        ),
        layers.BatchNormalization(),
        layers.MaxPooling2D((2, 2)),

        layers.Conv2D(
            filters=params['filters_4'],
            kernel_size=(3, 3),
            activation='relu',
            kernel_regularizer=regularizers.l2(params['l2_reg'])
        ),
        layers.BatchNormalization(),
        layers.MaxPooling2D((2, 2)),

        layers.Flatten(),

        layers.Dense(
            units=params['dense_units'],
            activation='relu',
            kernel_regularizer=regularizers.l2(params['l2_reg'])
        ),
        layers.BatchNormalization(),
        layers.Dropout(params['dropout_rate']),

        layers.Dense(num_classes, activation='softmax')
    ])

    model.compile(
        optimizer=Adam(learning_rate=0.0005),  # Use a fixed learning rate
        loss='categorical_crossentropy',
        metrics=['accuracy']
    )

    # Define callbacks
    early_stopping = EarlyStopping(
        monitor='val_loss',
        patience=10,
        restore_best_weights=True
    )

    reduce_lr = ReduceLROnPlateau(
        monitor='val_loss',
        factor=0.2,
        patience=5,
        min_lr=0.00001
    )

    # Define checkpoint callback
    checkpoint_callback = ModelCheckpoint(
        filepath=os.path.join(checkpoint_dir, 'model_checkpoint.keras'),
        save_best_only=True,
        monitor='val_loss'
    )

    # Train the model
    history = model.fit(
        train_generator,
        epochs=epochs,
        steps_per_epoch=train_generator.samples // batch_size,
        validation_data=valid_generator,
        validation_steps=valid_generator.samples // batch_size,
        callbacks=[early_stopping, reduce_lr, checkpoint_callback]
    )

    # Evaluate the model
    loss, accuracy = model.evaluate(valid_generator, steps=valid_generator.samples // batch_size)
    return accuracy, loss, history

# Define random search parameters
num_trials = 20
filter_options = [32, 64, 128]
dense_units_options = [128, 256, 512]
dropout_rate_options = [0.3, 0.5, 0.7]
l2_reg_options = [0.0001, 0.001, 0.01]

def random_hyperparameter_combinations(num_trials):
    hyperparameter_combinations = []
    for _ in range(num_trials):
        params = {
            'filters_1': random.choice(filter_options),
            'filters_2': random.choice(filter_options),
            'filters_3': random.choice(filter_options),
            'filters_4': random.choice(filter_options),
            'dense_units': random.choice(dense_units_options),
            'dropout_rate': random.choice(dropout_rate_options),
            'l2_reg': random.choice(l2_reg_options)
        }
        hyperparameter_combinations.append(params)
    return hyperparameter_combinations

# Initialize results list
results = []

# Perform random search
random_combinations = random_hyperparameter_combinations(num_trials)

for index, params in enumerate(random_combinations):
    print(f"Testing combination {index + 1}/{num_trials}: {params}")

    accuracy, loss, history = build_and_train_model(params, train_generator, valid_generator)
    
    # Log results
    results.append({
        'filters_1': params['filters_1'],
        'filters_2': params['filters_2'],
        'filters_3': params['filters_3'],
        'filters_4': params['filters_4'],
        'dense_units': params['dense_units'],
        'dropout_rate': params['dropout_rate'],
        'l2_reg': params['l2_reg'],
        'accuracy': accuracy,
        'loss': loss
    })

    # Save results to CSV after each trial
    results_df = pd.DataFrame(results)
    results_df.to_csv(r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\models\checkpoints\random_search_results.csv', index=False)

print("Random search results saved to random_search_results.csv")

Testing combination 1/20: {'filters_1': 128, 'filters_2': 64, 'filters_3': 128, 'filters_4': 128, 'dense_units': 256, 'dropout_rate': 0.7, 'l2_reg': 0.0001}
Epoch 1/20
413/413 ━━━━━━━━━━━━━━━━━━━━ 555s 1s/step - accuracy: 0.0351 - loss: 5.8016 - val_accuracy: 0.0362 - val_loss: 5.3857 - learning_rate: 5.0000e-04
Epoch 2/20
413/413 ━━━━━━━━━━━━━━━━━━━━ 1s 521us/step - accuracy: 0.0938 - loss: 4.1825 - val_accuracy: 0.0000e+00 - val_loss: 4.9505 - learning_rate: 5.0000e-04
Epoch 3/20
413/413 ━━━━━━━━━━━━━━━━━━━━ 550s 1s/step - accuracy: 0.2261 - loss: 3.5713 - val_accuracy: 0.5371 - val_loss: 2.2846 - learning_rate: 5.0000e-04
Epoch 4/20
413/413 ━━━━━━━━━━━━━━━━━━━━ 1s 459us/step - accuracy: 0.4375 - loss: 2.6927 - val_accuracy: 0.7143 - val_loss: 1.5891 - learning_rate: 5.0000e-04
Epoch 5/20
413/413 ━━━━━━━━━━━━━━━━━━━━ 544s 1s/step - accuracy: 0.4611 - loss: 2.2933 - val_accuracy: 0.4510 - val_loss: 2.4396 - learning_rate: 5.0000e-04
Epoch 6/20
413/413 ━━━━━━━━━━━━━━━━━━━━ 1s 474us/ste

: 

In [4]:
# Define CNN model
model = Sequential([
    InputLayer(input_shape=(150, 150, 3)),
    layers.Conv2D(48, (3, 3), activation=keras.activations.swish, kernel_regularizer=regularizers.l2(0.00015981491240774103,)),
    BatchNormalization(),
    MaxPooling2D((2, 2)),

    Conv2D(64, (3, 3), activation='relu', kernel_regularizer=regularizers.l2(0.00015981491240774103,)),
    BatchNormalization(),
    MaxPooling2D((2, 2)),

    Conv2D(192, (3, 3), activation='relu', kernel_regularizer=regularizers.l2(0.00015981491240774103,)),
    BatchNormalization(),
    MaxPooling2D((2, 2)),

    Conv2D(384, (3, 3), activation='relu', kernel_regularizer=regularizers.l2(0.00015981491240774103,)),
    BatchNormalization(),
    MaxPooling2D((2, 2)),

    Flatten(),

    Dense(256, activation='relu', kernel_regularizer=regularizers.l2(0.00015981491240774103,)),
    BatchNormalization(),
    Dropout(0.5),

    Dense(num_classes2, activation='softmax')
])

# Compile model
model.compile(
    optimizer=Adam(learning_rate=0.0005341180438864359),
    loss='categorical_crossentropy',
    metrics=['accuracy']
)

# Print model summary
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d (Conv2D)                 │ (None, 148, 148, 48)   │         1,344 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 148, 148, 48)   │           192 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d (MaxPooling2D)    │ (None, 74, 74, 48)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_1 (Conv2D)               │ (None, 72, 72, 64)     │        27,712 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 72, 72, 64)     │           256 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_1 (MaxPooling2D)  │ (None, 36, 36, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_2 (Conv2D)               │ (None, 34, 34, 192)    │       110,784 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_2           │ (None, 34, 34, 192)    │           768 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_2 (MaxPooling2D)  │ (None, 17, 17, 192)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_3 (Conv2D)               │ (None, 15, 15, 384)    │       663,936 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_3           │ (None, 15, 15, 384)    │         1,536 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_3 (MaxPooling2D)  │ (None, 7, 7, 384)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten (Flatten)               │ (None, 18816)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 256)            │     4,817,152 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_4           │ (None, 256)            │         1,024 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 147)            │        37,779 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 5,662,483 (21.60 MB)

 Trainable params: 5,660,595 (21.59 MB)

 Non-trainable params: 1,888 (7.38 KB)

In [5]:
# Define training callbacks
early_stopping = EarlyStopping(
    monitor='val_loss',
    patience=10,  # Number of epochs to wait before stopping if no improvement
    restore_best_weights=True
)

reduce_lr = ReduceLROnPlateau(
    monitor='val_loss',
    factor=0.2,  # Reduce learning rate by a factor of 0.2
    patience=5,  # Number of epochs with no improvement to wait before reducing
    min_lr=0.00001  # Minimum learning rate
)

# Define training parameters
epochs = 40  # Adjust based on your requirements

# Train the model
history2 = model.fit(
    train_generator2,
    epochs=epochs,
    steps_per_epoch=train_generator2.samples // batch_size2,
    validation_data=valid_generator2,
    validation_steps=valid_generator2.samples // batch_size2,
    callbacks=[early_stopping, reduce_lr]
)

# Save the model
model.save(r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\models\model06.keras')

Epoch 1/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 391s 470ms/step - accuracy: 0.0709 - loss: 5.0913 - val_accuracy: 0.3508 - val_loss: 3.0555 - learning_rate: 5.3412e-04
Epoch 2/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 0s 147us/step - accuracy: 0.3125 - loss: 2.9461 - val_accuracy: 0.6429 - val_loss: 2.0552 - learning_rate: 5.3412e-04
Epoch 3/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 397s 480ms/step - accuracy: 0.4420 - loss: 2.5662 - val_accuracy: 0.7284 - val_loss: 1.5276 - learning_rate: 5.3412e-04
Epoch 4/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 0s 121us/step - accuracy: 0.6875 - loss: 1.6774 - val_accuracy: 1.0000 - val_loss: 0.7942 - learning_rate: 5.3412e-04
Epoch 5/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 398s 482ms/step - accuracy: 0.6857 - loss: 1.5732 - val_accuracy: 0.8036 - val_loss: 1.1555 - learning_rate: 5.3412e-04
Epoch 6/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 1s 127us/step - accuracy: 0.6250 - loss: 1.3656 - val_accuracy: 1.0000 - val_loss: 0.7604 - learning_rate: 5.3412e-04
Epoch 7/40
826/826 ━━━━━━━━━━━━━━━━━━━━ 395s 4

In [6]:
import json

# Get the class indices (this is a dictionary: {class_name: class_index})
class_indices = train_generator2.class_indices
print("Class Indices:", class_indices)

# Save the class indices to a JSON file for future use
with open('class_indices.json', 'w') as f:
    json.dump(class_indices, f)

Class Indices: {'151': 0, 'Ancient Origins': 1, 'Aquapolis': 2, 'Arceus': 3, 'Astral Radiance': 4, 'BREAKpoint': 5, 'BREAKthrough': 6, 'Base': 7, 'Base Set 2': 8, 'Battle Styles': 9, 'Best of Game': 10, 'Black & White': 11, 'Black Star Promos': 12, 'Boundaries Crossed': 13, 'Brilliant Stars': 14, 'Burning Shadows': 15, 'Call of Legends': 16, 'Celebrations': 17, 'Celebrations Classic Collection': 18, 'Celestial Storm': 19, "Champion's Path": 20, 'Chilling Reign': 21, 'Cosmic Eclipse': 22, 'Crimson Invasion': 23, 'Crown Zenith': 24, 'Crystal Guardians': 25, 'Dark Explorers': 26, 'Darkness Ablaze': 27, 'Delta Species': 28, 'Deoxys': 29, 'Detective Pikachu': 30, 'Diamond & Pearl': 31, 'Double Crisis': 32, 'Dragon': 33, 'Dragon Frontiers': 34, 'Dragon Majesty': 35, 'Dragon Vault': 36, 'Dragons Exalted': 37, 'EX Trainer Kit 2 Minun': 38, 'EX Trainer Kit 2 Plusle': 39, 'EX Trainer Kit Latias': 40, 'EX Trainer Kit Latios': 41, 'Emerald': 42, 'Emerging Powers': 43, 'Evolutions': 44, 'Evolving S

In [3]:
# Load the test data
cnn_base_path = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN'
test_path = os.path.join(cnn_base_path, 'test')

target_size2 = (150, 150)
batch_size2 = 16

test_datagen = ImageDataGenerator(rescale=1./255)

test_generator = test_datagen.flow_from_directory(
    test_path,
    target_size=target_size2,
    batch_size=batch_size2,
    class_mode='categorical',
    shuffle=False
)

# Load the trained model
model = load_model(r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\models\model04.keras')

# Evaluate the model on the test set
test_loss, test_acc = model.evaluate(test_generator, verbose=2)
print(f"Test Accuracy: {test_acc}")
print(f"Test Loss: {test_loss}")

# Make predictions on the test set
predictions = model.predict(test_generator)

# Convert the predicted probabilities to class indices
predicted_classes = np.argmax(predictions, axis=1)

# Get the true class labels from the test generator
true_classes = test_generator.classes
class_labels = list(test_generator.class_indices.keys())

# Step 5: Generate classification report and confusion matrix
print("Classification Report:")
print(classification_report(true_classes, predicted_classes, target_names=class_labels))

print("Confusion Matrix:")
print(confusion_matrix(true_classes, predicted_classes))

Found 2940 images belonging to 147 classes.
184/184 - 18s - 97ms/step - accuracy: 0.9350 - loss: 0.4789
Test Accuracy: 0.9350340366363525
Test Loss: 0.47887563705444336
184/184 ━━━━━━━━━━━━━━━━━━━━ 16s 84ms/step
Classification Report:
                                 precision    recall  f1-score   support

                            151       1.00      0.95      0.97        20
                Ancient Origins       1.00      1.00      1.00        20
                      Aquapolis       1.00      0.95      0.97        20
                         Arceus       1.00      1.00      1.00        20
                Astral Radiance       0.95      1.00      0.98        20
                     BREAKpoint       1.00      1.00      1.00        20
                   BREAKthrough       0.95      0.90      0.92        20
                           Base       0.79      0.75      0.77        20
                     Base Set 2       1.00      1.00      1.00        20
                  Battle Styles   

In [4]:
# Load the test data
cnn_base_path = r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\CNN'
test_path2 = os.path.join(cnn_base_path, 'test')

target_size2 = (150, 150)
batch_size2 = 16

test_datagen2 = ImageDataGenerator(rescale=1./255)

test_generator2 = test_datagen2.flow_from_directory(
    test_path2,
    target_size=target_size2,
    batch_size=batch_size2,
    class_mode='categorical',
    shuffle=False
)

# Load the trained model
model2 = load_model(r'C:\Users\Jimmy\Desktop\final-project\PokemonTCG\models\model06.keras')

# Evaluate the model on the test set
test_loss2, test_acc2 = model2.evaluate(test_generator2, verbose=2)
print(f"Test Accuracy: {test_acc2}")
print(f"Test Loss: {test_loss2}")

# Make predictions on the test set
predictions2 = model2.predict(test_generator2)

# Convert the predicted probabilities to class indices
predicted_classes2 = np.argmax(predictions2, axis=1)

# Get the true class labels from the test generator
true_classes2 = test_generator2.classes
class_labels2 = list(test_generator2.class_indices.keys())

# Generate classification report and confusion matrix
print("Classification Report:")
print(classification_report(true_classes2, predicted_classes2, target_names=class_labels2))

print("Confusion Matrix:")
print(confusion_matrix(true_classes2, predicted_classes2))

Found 2940 images belonging to 147 classes.
184/184 - 16s - 89ms/step - accuracy: 0.9320 - loss: 0.4627
Test Accuracy: 0.9319728016853333
Test Loss: 0.46266329288482666
184/184 ━━━━━━━━━━━━━━━━━━━━ 16s 84ms/step
Classification Report:
                                 precision    recall  f1-score   support

                            151       1.00      0.95      0.97        20
                Ancient Origins       1.00      1.00      1.00        20
                      Aquapolis       1.00      0.90      0.95        20
                         Arceus       1.00      1.00      1.00        20
                Astral Radiance       1.00      1.00      1.00        20
                     BREAKpoint       0.95      0.95      0.95        20
                   BREAKthrough       0.86      0.90      0.88        20
                           Base       0.75      0.75      0.75        20
                     Base Set 2       1.00      1.00      1.00        20
                  Battle Styles   